In [89]:
import random
from deap import base
from deap import creator
from deap import tools
import pandas as pd
from shapely.geometry import MultiLineString, MultiPolygon
from shapely.geometry import Point, LineString, Polygon, MultiPoint
from shapely.ops import unary_union, nearest_points
from matplotlib import pyplot, rcParams
from math import sin, cos, pi
from shapely.geometry import Point, LineString, Polygon
from shapely.ops import unary_union
from matplotlib import pyplot, rcParams
from deap import algorithms
from deap import benchmarks
from deap.benchmarks.tools import diversity, convergence, hypervolume
import array
import json
import numpy
import matplotlib.pyplot as plt
from math import sqrt
from deap import algorithms
import math
from shapely.geometry import Point, Polygon, LineString
from shapely.geometry import MultiPolygon, MultiPoint
import pprint
from shapely.geometry import Point, Polygon, LineString
import shapely as sh
from math import factorial
import pymop.factory
from deap.benchmarks.tools import igd
import copy

In [90]:
# air base boundary (interested Area)
air_base = Polygon([(10,10), (0,20),(0,40),(20,60),(80,100),(90,130),(110,140),(140,130),(160,140),(180,130),(180,110),(210,70),(190,40),(150,50),(130,40),(110,50),(30,10)])   
# run way boundary(Key Area)
air_way = Polygon([(38,34),(32,42),(132,104),(108,120),(110,122),(136,106),(156,116),(158,110),(152,94),(186,68),(182,64),(158,78),(136,78),(126,72),(118,80)])


In [91]:
place1 = Polygon([(22, 44), (108, 98), (110, 114), (124, 102), (24, 40)])
placement_list = []
for x in range(0, 200):
    for y in range(0, 200):
        canvas = Point(x, y)
        if (place1.contains(canvas) == True):
            placement_list.append(canvas)
place2 = Polygon([(138, 114),(160,124),(166,118),(160,116),(156,120),(140,110)])
for x in range(0, 200):
    for y in range(0, 200):
        canvas = Point(x, y)
        if (place2.contains(canvas) == True):
            placement_list.append(canvas)
place3 = Polygon([(158,104),(164,112),(168,96),(162,94)])
for x in range(0, 200):
    for y in range(0, 200):
        canvas = Point(x, y)
        if (place3.contains(canvas) == True):
            placement_list.append(canvas)
place4 = Polygon([(152,76),(158,76),(176,64),(174,60),(154,72)])
for x in range(0, 200):
    for y in range(0, 200):
        canvas = Point(x, y)
        if (place4.contains(canvas) == True):
            placement_list.append(canvas)
place5 = Polygon([(48,38),(118,76),(126,68),(118,64),(108,66),(54,39)])
for x in range(0, 200):
    for y in range(0, 200):
        canvas = Point(x, y)
        if (place5.contains(canvas) == True):
            placement_list.append(canvas)
area = []
for i in range (len(placement_list)):
    xy = (placement_list[i].x, placement_list[i].y)
    area.append(xy)
items = {i : area[i] for i in range(len(area))}
print("Number of available position", len(items))

Number of available position 1250


In [92]:

Pouplation_size = 10000000  # population size
NOBJ = 3                    # Number of objective function 3

creator.create("FitnessMax", base.Fitness, weights=(1.0, 1.0, -1.0))   
creator.create("Individual", list, fitness=creator.FitnessMax)     
toolbox = base.Toolbox()            

C:\Users\AJOU\Anaconda3\lib\site-packages\deap\creator.py:141: RuntimeWarning: A class named 'FitnessMax' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  RuntimeWarning)
C:\Users\AJOU\Anaconda3\lib\site-packages\deap\creator.py:141: RuntimeWarning: A class named 'Individual' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  RuntimeWarning)


In [93]:
ang_sample = range(0, 359, 10)
# step of view angle

In [94]:
#  list of (view angle, cost, radius)
list_angle = [30, 80, 60, 90, 180]
list_cost = [10000, 13000, 15000, 18000, 20000]
list_radius = [200, 130, 150, 120, 100]
budget = 100000

In [95]:
# make obstacle
obstacle = Polygon([(0,20),(50,20),(50,30),(40,30), (42,33),(36,30),(0, 30)])
obs_bound = obstacle.boundary


In [108]:
IND_INIT_SIZE = 4
ang_sample = range(0, 359, 10)
def attr_cam():
    x = random.randint(0, 4)
    return x
toolbox.register("attr_cam", attr_cam)    

def attr_angle():
    x = random.randint(0, len(ang_sample))
    return x*10
toolbox.register("attr_angle", attr_angle)    
def attr():
    x = random.randint(0, len(area)-1)
    return x
toolbox.register("attr_float", attr)    

func_seq = [attr_cam , attr_angle, attr]




In [109]:
func_seq = [attr_cam , attr_angle, attr]
def attr_place():
    func_seq = [attr_cam , attr_angle, attr]
    return tools.initCycle(list, func_seq)
toolbox.register("attr_place", attr_place)    


In [110]:
toolbox.register("individual", tools.initRepeat, creator.Individual, 
    toolbox.attr_place, IND_INIT_SIZE)
toolbox.register("population", tools.initRepeat, list, toolbox.individual)


In [111]:
# line of sight sector 
def LOS_sector(center, start_angle, end_angle, radius, steps=1):
    def polar_point(origin_point, angle,  distance): 
        return [origin_point.x + math.sin(math.radians(angle)) * distance, origin_point.y + math.cos(math.radians(angle)) * distance]
    if start_angle < 0:
        start_angle = start_angle + 360
    if end_angle > 360:
        end_angle = end_angle - 360
    if start_angle > end_angle:
        start_angle = start_angle - 360
    else:
        pass
    step_angle_width = steps
    sector_width = (end_angle-start_angle) 
    
    segment_vertices = []
    for z in range(0, sector_width):
        if LineString([(polar_point(center, start_angle + z * step_angle_width,radius)), center]).intersects(obstacle) is False:
            segment_vertices.append((polar_point(center, start_angle + z * step_angle_width,radius)))
        elif LineString([(polar_point(center, start_angle + z * step_angle_width,radius)), center]).intersects(obstacle) is True : 
            cross_points = obs_bound.intersection(LineString([(polar_point(center, start_angle + z * step_angle_width, radius)), center]))
            LOS_distance = center.distance(cross_points)
            distance_list = []
            if isinstance(cross_points, sh.geometry.Point) :
                   segment_vertices.append((polar_point(center, start_angle + z * step_angle_width,LOS_distance)))
            else:
                N_cxp = len(list(cross_points))
                dist_list = []
                for k in range(0, (N_cxp)):
                    dist_list.append(center.distance(cross_points[k]))
                min_index = dist_list.index(LOS_distance)
                segment_vertices.append((polar_point(center, start_angle + z * step_angle_width,LOS_distance)))
        else :
            print("error?")
    segment_vertices.append(polar_point(center, 0,0))
    return Polygon(segment_vertices)

In [112]:
def eval_anti_UAS(individual):
    cover = Point(-9999, -9999)
    COST = 0
    area = 0
    for item in individual:  
        angle = item[1] 
        center = Point(items[item[2]])
        start_angle = int(angle - (list_angle[item[0]])*0.5)
        end_angle = int(start_angle + (list_angle[item[0]]))        
        radius = list_radius[item[0]]
        solo_area = LOS_sector(center, start_angle, end_angle, radius)
        cover = cover.union(solo_area)
        final_cover = cover.difference(Point(-9999,-9999))
        air_way_intersect = air_way.intersection(final_cover)        
        CKD = -(100-(air_way_intersect.area/air_way.area*100))
        intersect = air_base.intersection(final_cover)
        CID = -(100-(intersect.area/air_base.area*100))
        COST += list_cost[item[0]]
    return CKD, CID, COST
    
toolbox.register("evaluate", eval_anti_UAS)  
toolbox.evaluate(toolbox.individual())

(-8.925133792317737, -34.73755190545579, 66000)

In [113]:
toolbox.register("select", tools.selNSGA2)

In [114]:
def par_min(ind1, ind2):
    parents_tuple = ind1 + ind2

    cost_list = []
    for i in parents_tuple:
        temp_cost = [list_cost[i[0]]]
        cost_list = cost_list + temp_cost
    parents_min = min(cost_list)
    return parents_min
def par_max(ind1, ind2):
    parents_tuple = ind1 + ind2

    cost_list = []
    for i in parents_tuple:
        temp_cost = [list_cost[i[0]]]
        cost_list = cost_list + temp_cost
    parents_max = max(cost_list)
    return parents_max
par_max(toolbox.individual(), toolbox.individual())

20000

In [136]:
def cxSet(ind1, ind2):
    
    Ind_Size = 0
    price = 0
    first_ind = []
    choice_ind = []
    ind1 = list(map(toolbox.clone, ind1))
    ind2 = list(map(toolbox.clone, ind2))
    ind3 = list(map(toolbox.clone, ind1))
    ind4 = list(map(toolbox.clone, ind2))
    sum_list = ind1 + ind2
    choice_list = []
    
    while len(first_ind) < IND_INIT_SIZE :
        choice_list = random.choice(sum_list)
        sum_list.remove(choice_list)
        first_ind = first_ind + [choice_list]                
    else : 
        pass
    
    ind1 = first_ind
    second_ind = []
    choice_list = []
    sum_list = ind3 + ind4
    
    
    while len(second_ind) < IND_INIT_SIZE :
        choice_list = random.choice(sum_list)
        sum_list.remove(choice_list)
        second_ind = second_ind + [choice_list]                
    else : 
        pass   
    ind2 = second_ind
    
    #del ind1.fitness.values
    #del ind2.fitness.values
    
    return ind1, ind2
toolbox.register("mate", cxSet)

origin1 = toolbox.individual()
origin2 = toolbox.individual()
print("origin1", origin1)
print("origin2", origin2)
toolbox.mate(origin1, origin2)

origin1 [[1, 90, 587], [0, 130, 287], [3, 120, 1051], [3, 90, 456]]
origin2 [[4, 220, 968], [4, 160, 795], [2, 220, 497], [4, 340, 722]]


([[3, 120, 1051], [4, 340, 722], [3, 90, 456], [2, 220, 497]],
 [[4, 160, 795], [1, 90, 587], [3, 120, 1051], [3, 90, 456]])

In [142]:
def mutSet(individual):
    empty = []
    for item in individual:
        List_item = list(item)
        if random.random() < 0.5:
            mut_place = item[2] + random.randint(-100,100)
            if mut_place < 0 : 
                mut_place = mut_place + len(items)
            elif mut_place > len(items)-1 :
                mut_place = mut_place - len(items)
            else :
                pass
            item[2] = mut_place            
        if random.random() < 0.5:
            mut_ang = item[1] + 10*random.randint(-9,9)
            if mut_ang < 0 :
                mut_ang = mut_ang + 360
            elif mut_ang > 360 :
                mut_ang = mut_ang - 360
            else :
                pass
            item[1] = mut_ang
        else :
            pass
        
        empty = empty + [item[0]]
    random.shuffle(empty)

    for k in range (len(individual)):
        individual[k][0] = empty[k]
    
    
    return individual
toolbox.register("mutate", mutSet)
toolbox.mutate(toolbox.individual())

[[1, 210, 145], [3, 110, 638], [0, 250, 1001], [4, 90, 811]]

In [145]:
def main():
    pareto = tools.ParetoFront()
    NGEN = 10
    MU = 20
    LAMBDA = 500
    CXPB = 0.5
    MUTPB = 0.5

    stats = tools.Statistics(lambda ind: ind.fitness.values)
    
    stats.register("avg", numpy.mean, axis=0)
    stats.register("std", numpy.std, axis=0)
    stats.register("min", numpy.min, axis=0)
    stats.register("max", numpy.max, axis=0)
    logbook = tools.Logbook()
    logbook.header = "gen", "evals", "std", "min", "avg", "max"
    pop = toolbox.population(n=MU)
    
    hof = tools.ParetoFront()

    # Evaluate the individuals with an invalid fitness
    
    invalid_ind = [ind for ind in pop if not ind.fitness.valid]

    fitnesses = toolbox.map(toolbox.evaluate, invalid_ind)
    for ind, fit in zip(invalid_ind, fitnesses):
        ind.fitness.values = fit
     
    # Compile statistics about the population
    record = stats.compile(pop)
    logbook.record(gen=0, evals=len(invalid_ind), **record)
    print(logbook.stream)
    
    # Begin the generational process
    if pareto is not None:
        pareto.update(pop)
    #print("pop", pop)
    for gen in range(1, NGEN):
        #print("pop", pop)
        offspring = algorithms.varAnd(pop, toolbox, CXPB, MUTPB)

        # Evaluate the offspring
        fitnesses = toolbox.map(toolbox.evaluate, offspring)
        for ind in offspring :
            ind.fitness.values = toolbox.evaluate(ind)
        

        # Evaluate the individuals with an invalid fitness       
        invalid_ind = [ind for ind in offspring if not ind.fitness.valid]
        fitnesses = toolbox.map(toolbox.evaluate, invalid_ind)
        for ind, fit in zip(invalid_ind, fitnesses):
            ind.fitness.values = fit
            
            
        # Select the next generation population from parents and offspring
        
        pop = toolbox.select(pop + offspring, MU)
        
        # Compile statistics about the new population
        record = stats.compile(pop) 
        logbook.record(gen=gen, evals=len(invalid_ind), **record)
        print(logbook.stream)
        
        pareto.update(pop)
        print(len(pareto))
    print(len(hof))
    return pop, logbook, pareto
    
main()

gen	evals	std                                        	min                                           	avg                                              	max                                              
0  	20   	[  20.59872251   12.86215979 5548.8737596 ]	[  -66.04821748   -64.79032494 45000.        ]	[-3.15213729e+01 -3.87229643e+01  5.91000000e+04]	[-0.00000000e+00 -9.47735067e+00  7.10000000e+04]


AttributeError: 'list' object has no attribute 'fitness'